#pre-processing data
classify care duration for the next week. Duration after 15 hours are categorized into 5 groups: 16,17,18,19,20

Features are selected in R

In [2]:
sqlContext.clearCache()
from pyspark.sql.types import StructType, StructField, IntegerType, StringType
# df = sqlContext.read.format('csv').options(header='true').load("/FileStore/tables/allCom_60_v2.csv").drop("PatientID").withColumnRenamed('duration_next_week_category','label')

df = sqlContext.read.format('csv').options(header='true').load("/FileStore/tables/allCom_v1_categorized.csv").withColumnRenamed('duration_next_week_cat','label').drop("duration_next_week").drop("iterats")
df.cache()


Out[ 39 ]: DataFrame[label: string, Estimated_CareMoments_Weekly: string, Estimated_Minutes_Weekly: string, Advice_Instructions_Travel: string, Treatments: string, Case_management: string, Monitoring_Bevaking: string, psychosocial_num: string, physiological_num: string, healthRelated_num: string, ass_week_num: string, ass_year_day: string, register_NextWeekNR: string, duration_mean_each_time: string, duration_median_each_time: string, care_times_weekly: string, duration_week_minus: string, duration_each_time: string, Age: string, ass_date: string, ass_weekday: string, ass_month: string, ass_month_day: string, ass_quater_day: string, reg_date: string, reg_weekDay: string, reg_month: string, reg_month_day: string, reg_quater_day: string, estimated_care_duration.Less.than.3.months: string, estimated_care_duration.Longer.than.6.months: string, estimated_care_request.Decreasing.Care: string, estimated_care_request.Increasing.Care: string, estimated_care_request.Stable.care.demand: string, TeamID.0: string, ProblemName.Personal.care: string, ProblemName.Skin: string, combindSymptonProblemomittedSymptons: string]

In [3]:
df.printSchema()

root
-- label: string (nullable = true)
-- Estimated_CareMoments_Weekly: string (nullable = true)
-- Estimated_Minutes_Weekly: string (nullable = true)
-- Advice_Instructions_Travel: string (nullable = true)
-- Treatments: string (nullable = true)
-- Case_management: string (nullable = true)
-- Monitoring_Bevaking: string (nullable = true)
-- psychosocial_num: string (nullable = true)
-- physiological_num: string (nullable = true)
-- healthRelated_num: string (nullable = true)
-- ass_week_num: string (nullable = true)
-- ass_year_day: string (nullable = true)
-- register_NextWeekNR: string (nullable = true)
-- duration_mean_each_time: string (nullable = true)
-- duration_median_each_time: string (nullable = true)
-- care_times_weekly: string (nullable = true)
-- duration_week_minus: string (nullable = true)
-- duration_each_time: string (nullable = true)
-- Age: string (nullable = true)
-- ass_date: string (nullable = true)
-- ass_weekday: string (nullable = true)
-- ass_month: string (nullable = true)
-- ass_month_day: string (nullable = true)
-- ass_quater_day: string (nullable = true)
-- reg_date: string (nullable = true)
-- reg_weekDay: string (nullable = true)
-- reg_month: string (nullable = true)
-- reg_month_day: string (nullable = true)
-- reg_quater_day: string (nullable = true)
-- estimated_care_duration.Less.than.3.months: string (nullable = true)
-- estimated_care_duration.Longer.than.6.months: string (nullable = true)
-- estimated_care_request.Decreasing.Care: string (nullable = true)
-- estimated_care_request.Increasing.Care: string (nullable = true)
-- estimated_care_request.Stable.care.demand: string (nullable = true)
-- TeamID.0: string (nullable = true)
-- ProblemName.Personal.care: string (nullable = true)
-- ProblemName.Skin: string (nullable = true)
-- combindSymptonProblemomittedSymptons: string (nullable = true)

In [4]:
print "Our dataset has %d rows." % df.count()

Our dataset has 642418 rows.

In [5]:
for col in df.columns:
  df = df.withColumnRenamed(col,col.replace(".", "_"))

In [6]:
df.printSchema()

root
-- label: string (nullable = true)
-- Estimated_CareMoments_Weekly: string (nullable = true)
-- Estimated_Minutes_Weekly: string (nullable = true)
-- Advice_Instructions_Travel: string (nullable = true)
-- Treatments: string (nullable = true)
-- Case_management: string (nullable = true)
-- Monitoring_Bevaking: string (nullable = true)
-- psychosocial_num: string (nullable = true)
-- physiological_num: string (nullable = true)
-- healthRelated_num: string (nullable = true)
-- ass_week_num: string (nullable = true)
-- ass_year_day: string (nullable = true)
-- register_NextWeekNR: string (nullable = true)
-- duration_mean_each_time: string (nullable = true)
-- duration_median_each_time: string (nullable = true)
-- care_times_weekly: string (nullable = true)
-- duration_week_minus: string (nullable = true)
-- duration_each_time: string (nullable = true)
-- Age: string (nullable = true)
-- ass_date: string (nullable = true)
-- ass_weekday: string (nullable = true)
-- ass_month: string (nullable = true)
-- ass_month_day: string (nullable = true)
-- ass_quater_day: string (nullable = true)
-- reg_date: string (nullable = true)
-- reg_weekDay: string (nullable = true)
-- reg_month: string (nullable = true)
-- reg_month_day: string (nullable = true)
-- reg_quater_day: string (nullable = true)
-- estimated_care_duration_Less_than_3_months: string (nullable = true)
-- estimated_care_duration_Longer_than_6_months: string (nullable = true)
-- estimated_care_request_Decreasing_Care: string (nullable = true)
-- estimated_care_request_Increasing_Care: string (nullable = true)
-- estimated_care_request_Stable_care_demand: string (nullable = true)
-- TeamID_0: string (nullable = true)
-- ProblemName_Personal_care: string (nullable = true)
-- ProblemName_Skin: string (nullable = true)
-- combindSymptonProblemomittedSymptons: string (nullable = true)

In [7]:
from pyspark.ml import Pipeline
from pyspark.ml.feature import OneHotEncoderEstimator, StringIndexer, VectorAssembler
from pyspark.sql.functions import col  # for indicating a column using a string in the line below
df = df.select([col(c).cast("double").alias(c) for c in df.columns])
# test = test.select([col(c).cast("double").alias(c) for c in test.columns])
df.printSchema()

root
-- label: double (nullable = true)
-- Estimated_CareMoments_Weekly: double (nullable = true)
-- Estimated_Minutes_Weekly: double (nullable = true)
-- Advice_Instructions_Travel: double (nullable = true)
-- Treatments: double (nullable = true)
-- Case_management: double (nullable = true)
-- Monitoring_Bevaking: double (nullable = true)
-- psychosocial_num: double (nullable = true)
-- physiological_num: double (nullable = true)
-- healthRelated_num: double (nullable = true)
-- ass_week_num: double (nullable = true)
-- ass_year_day: double (nullable = true)
-- register_NextWeekNR: double (nullable = true)
-- duration_mean_each_time: double (nullable = true)
-- duration_median_each_time: double (nullable = true)
-- care_times_weekly: double (nullable = true)
-- duration_week_minus: double (nullable = true)
-- duration_each_time: double (nullable = true)
-- Age: double (nullable = true)
-- ass_date: double (nullable = true)
-- ass_weekday: double (nullable = true)
-- ass_month: double (nullable = true)
-- ass_month_day: double (nullable = true)
-- ass_quater_day: double (nullable = true)
-- reg_date: double (nullable = true)
-- reg_weekDay: double (nullable = true)
-- reg_month: double (nullable = true)
-- reg_month_day: double (nullable = true)
-- reg_quater_day: double (nullable = true)
-- estimated_care_duration_Less_than_3_months: double (nullable = true)
-- estimated_care_duration_Longer_than_6_months: double (nullable = true)
-- estimated_care_request_Decreasing_Care: double (nullable = true)
-- estimated_care_request_Increasing_Care: double (nullable = true)
-- estimated_care_request_Stable_care_demand: double (nullable = true)
-- TeamID_0: double (nullable = true)
-- ProblemName_Personal_care: double (nullable = true)
-- ProblemName_Skin: double (nullable = true)
-- combindSymptonProblemomittedSymptons: double (nullable = true)

In [8]:
# pack features 
from pyspark.ml.feature import VectorAssembler, VectorIndexer
featuresCols = df.columns
featuresCols.remove('label')
# featuresCols.remove('weights')
# featuresCols.remove('Marital_statusAlleenstaand')
# featuresCols.remove('Marital_statusGehuwd')
# featuresCols.remove('Marital_statusSamenwonend')
# featuresCols.remove('Marital_statusSamenwonend_met_contract')
# This concatenates all feature columns into a single feature vector in a new column "rawFeatures".
vectorAssembler = VectorAssembler(inputCols=featuresCols, outputCol="rawFeatures")
# This identifies categorical features and indexes them.
vectorIndexer = VectorIndexer(inputCol="rawFeatures", outputCol="features", maxCategories=2)

In [9]:
display(df.select('label').distinct())

label 8.0 7.0 29.0 18.0 1.0 25.0 4.0 23.0 31.0 11.0 21.0 14.0 22.0 3.0 19.0 28.0 2.0 17.0 27.0 10.0 30.0 13.0 6.0 20.0 5.0 15.0 24.0 9.0 26.0 16.0 12.0

In [10]:
from pyspark.ml import Pipeline
pipeline = Pipeline(stages=[vectorAssembler, vectorIndexer])
pipelineModel = pipeline.fit(df)
df = pipelineModel.transform(df)
# display(df)
(trainingData, testData) = df.randomSplit([0.7, 0.3], seed=100)
print(trainingData.count())
print(testData.count())

449913
192505

#logistic regression
tried to use weight for different class since the data is imbalanced, but the result is not improved.

In [12]:
from pyspark.ml.classification import LogisticRegression
# elasticNetParam: For alpha = 0, the penalty is an L2 penalty. 
#For alpha = 1, it is an L1 penalty. For alpha in (0,1), the penalty is a combination of L1 and L2. Default is 0.0 which is an L2 penalty.
# regParam: Set the regularization parameter. Default is 0.0.
# default:100
# lr =  LogisticRegression(maxIter=50, regParam=0.0, elasticNetParam=0.0,labelCol="label", featuresCol="features",weightCol="weights")
lr =  LogisticRegression(maxIter=50, regParam=0.0, elasticNetParam=0.0,labelCol="label", featuresCol="features")
lrModel = lr.fit(trainingData)
predictions = lrModel.transform(testData)
display(predictions)


label Estimated_CareMoments_Weekly Estimated_Minutes_Weekly Advice_Instructions_Travel Treatments Case_management Monitoring_Bevaking psychosocial_num physiological_num healthRelated_num ass_week_num ass_year_day register_NextWeekNR duration_mean_each_time duration_median_each_time care_times_weekly duration_week_minus duration_each_time Age ass_date ass_weekday ass_month ass_month_day ass_quater_day reg_date reg_weekDay reg_month reg_month_day reg_quater_day estimated_care_duration_Less_than_3_months estimated_care_duration_Longer_than_6_months estimated_care_request_Decreasing_Care estimated_care_request_Increasing_Care estimated_care_request_Stable_care_demand TeamID_0 ProblemName_Personal_care ProblemName_Skin combindSymptonProblemomittedSymptons rawFeatures features rawPrediction probability prediction 1.0 -2.42835361278535 -4.41505692051643 0.0 0.0 0.0 1.0 -1.07489125583662 -0.422573857940944 -1.28887010925821 30.0 209.0 31.0 -0.333472735371121 -0.596537638605271 -1.64879034295031 -1.71727082156315 1.16676467167333 0.900367377727457 28.0 6.0 7.0 28.0 28.0 26.0 4.0 7.0 26.0 26.0 1.88794608126386 -0.617985482268058 -0.661820249334744 -0.776632715218068 -0.406120359112696 0.54016919192849 -0.330597037409831 2.90520742954084 -1.14195356170005 List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, -0.422573857940944, -1.28887010925821, 30.0, 209.0, 31.0, -0.333472735371121, -0.596537638605271, -1.64879034295031, -1.71727082156315, 1.16676467167333, 0.900367377727457, 28.0, 6.0, 7.0, 28.0, 28.0, 26.0, 4.0, 7.0, 26.0, 26.0, 1.88794608126386, -0.617985482268058, -0.661820249334744, -0.776632715218068, -0.406120359112696, 0.54016919192849, -0.330597037409831, 2.90520742954084, -1.14195356170005)) List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, -0.422573857940944, -1.28887010925821, 30.0, 209.0, 31.0, -0.333472735371121, -0.596537638605271, -1.64879034295031, -1.71727082156315, 1.16676467167333, 0.900367377727457, 28.0, 6.0, 7.0, 28.0, 28.0, 26.0, 4.0, 7.0, 26.0, 26.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0)) List(1, 32, List(), List(-8.798806686253657, 19.456867778764757, 18.569288769540854, 17.251535309746934, 15.685798807045876, 14.460248140178688, 11.547587696669368, 8.909994995485583, 9.169285316948782, 4.8899605021116965, 3.8826373375190926, 2.89228573441582, 0.39656695012032783, 0.5159527556372269, -4.1629088032250445, -1.7959821395511506, -4.440825594546002, -1.5939780580042142, -4.0470538738571715, -9.53784670104814, -4.428800752767656, -7.49214288726854, -8.96314161220662, -8.003443268984078, -4.260407969170791, -6.191802496540964, -7.973801762010384, -10.61064553237312, -7.622923620135169, -7.329153331532538, -11.105212963933397, -9.269132040776377)) List(1, 32, List(), List(3.4498637961776516E-13, 0.6442960245707691, 0.26522520008683986, 0.07101036249002338, 0.014836484471954393, 0.004355932231257042, 2.3666212306352983E-4, 1.692921422127605E-5, 2.1940431087765447E-5, 3.039191059917454E-7, 1.1098981082079416E-7, 4.122672864760264E-8, 3.3986150666222114E-9, 3.829574961060569E-9, 3.5575156421975136E-11, 3.793936060646392E-10, 2.694319469760652E-11, 4.643220042205796E-10, 3.9944958551634684E-11, 1.6475588970460937E-13, 2.7269138132442137E-11, 1.2743209606872336E-12, 2.9270638597359454E-13, 7.64229666162602E-13, 3.2270334606786223E-11, 4.677453545394728E-12, 7.872216604117936E-13, 5.6354725161264805E-14, 1.1181021331673318E-12, 1.499906859662905E-12, 3.4367063839328334E-14, 2.1554712914474505E-13)) 1.0 1.0 -2.42835361278535 -4.41505692051643 0.0 0.0 0.0 1.0 -1.07489125583662 0.265702788042987 1.2690691336789 10.0 68.0 11.0 -0.686051986749209 -0.333889608030033 -2.43849521366943 -3.18127997658884 -0.857620455848467 1.0802194040719 9.0 5.0 3.0 9.0 68.0 9.0 5.0 3.0 9.0 68.0 -0.529675319282247 -0.617985482268058 -0.661820249334744 -0.776632715218068 -0.406120359112696 0.54016919192849 -0.330597037409831 -0.344208965326497 

In [13]:
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction", labelCol="label",metricName="f1")
print ("f1= ", evaluator.evaluate(predictions))
print("accuracy = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
print("weightedPrecision = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
print("weightedRecall = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

('f1= ', 0.2765762713818138)
('accuracy = ', 0.28548868860549076)
('weightedPrecision = ', 0.2830859916093512)
('weightedRecall = ', 0.2854886886054908)

In [14]:
trainingSummary = lrModel.summary
print("acc",trainingSummary.accuracy)
print("recall",trainingSummary.recallByLabel)
print("TP",trainingSummary.truePositiveRateByLabel)
print("weightedFalsePositive",trainingSummary.weightedFalsePositiveRate)
print("weightedFMeasure",trainingSummary.weightedFMeasure)
print("weightedPrecision",trainingSummary.weightedPrecision)
print("weightedRecall",trainingSummary.weightedRecall)
print("weightedTruePositiveRate",trainingSummary.weightedTruePositiveRate)

('acc', 0.28697103662263596)
('recall', [0.26864774624373955, 0.40497251647191584, 0.3046066664544268, 0.27131265680884004, 0.4367837210904665, 0.23035657936257495, 0.2662193032552827, 0.262590930196564, 0.35152284263959394, 0.198149066270038, 0.10461636421521808, 0.2280326700652305, 0.08212049760143102, 0.2693008011653314, 0.07308120133481646, 0.29133858267716534, 0.05579560398271651, 0.00028901734104046245, 0.39944328462073764, 0.31805425631431244, 0.3135476237428515, 0.2414075286415712, 0.04832585433206766, 0.5970125409377746, 0.35394003714513134, 0.0056, 0.3556789069171648, 0.48854961832061067, 0.0273492286115007, 0.7175853018372703, 0.6587374199451053])
('TP', [0.26864774624373955, 0.40497251647191584, 0.3046066664544268, 0.27131265680884004, 0.4367837210904665, 0.23035657936257495, 0.2662193032552827, 0.262590930196564, 0.35152284263959394, 0.198149066270038, 0.10461636421521808, 0.2280326700652305, 0.08212049760143102, 0.2693008011653314, 0.07308120133481646, 0.29133858267716534, 0.05579560398271651, 0.00028901734104046245, 0.39944328462073764, 0.31805425631431244, 0.3135476237428515, 0.2414075286415712, 0.04832585433206766, 0.5970125409377746, 0.35394003714513134, 0.0056, 0.3556789069171648, 0.48854961832061067, 0.0273492286115007, 0.7175853018372703, 0.6587374199451053])
('weightedFalsePositive', 0.04937325533026596)
('weightedFMeasure', <bound method LogisticRegressionTrainingSummary.weightedFMeasure of <pyspark.ml.classification.LogisticRegressionTrainingSummary object at 0x7fed0ba7c610>>)
('weightedPrecision', 0.28412333383512195)
('weightedRecall', 0.28697103662263584)
('weightedTruePositiveRate', 0.28697103662263584)

In [15]:
trainingData.columns

Out[ 51 ]: 
['label',
 'Estimated_CareMoments_Weekly',
 'Estimated_Minutes_Weekly',
 'Advice_Instructions_Travel',
 'Treatments',
 'Case_management',
 'Monitoring_Bevaking',
 'psychosocial_num',
 'physiological_num',
 'healthRelated_num',
 'ass_week_num',
 'ass_year_day',
 'register_NextWeekNR',
 'duration_mean_each_time',
 'duration_median_each_time',
 'care_times_weekly',
 'duration_week_minus',
 'duration_each_time',
 'Age',
 'ass_date',
 'ass_weekday',
 'ass_month',
 'ass_month_day',
 'ass_quater_day',
 'reg_date',
 'reg_weekDay',
 'reg_month',
 'reg_month_day',
 'reg_quater_day',
 'estimated_care_duration_Less_than_3_months',
 'estimated_care_duration_Longer_than_6_months',
 'estimated_care_request_Decreasing_Care',
 'estimated_care_request_Increasing_Care',
 'estimated_care_request_Stable_care_demand',
 'TeamID_0',
 'ProblemName_Personal_care',
 'ProblemName_Skin',
 'combindSymptonProblemomittedSymptons',
 'rawFeatures',
 'features']

grid search

In [17]:
# from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
# # Create ParamGrid for Cross Validation
# paramGrid = (ParamGridBuilder()
#              .addGrid(lr.regParam, [0.0, 0.2, 0.5])
#              .addGrid(lr.elasticNetParam, [0.0, 0.5, 1.0])
#              .addGrid(lr.maxIter, [100, 200, 300])
#              .build())
# cv = CrossValidator(estimator=lr, estimatorParamMaps=paramGrid, evaluator=evaluator, numFolds=5)
# # Run cross validations
# cvModel = cv.fit(trainingData)
# predictions = cvModel.transform(testData)

# print("Coefficients: \n" + str(cvModel.bestModel.coefficientMatrix ))
# print("Intercept: " + str(cvModel.bestModel.interceptVector))

In [18]:
# # evaluator = MulticlassClassificationEvaluator(predictionCol="prediction", labelCol="label",metricName="f1")
# print ("f1= ", evaluator.evaluate(predictions))
# print("accuracy = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
# print("weightedPrecision = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
# print("weightedRecall = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

#decision tree
simple decision tree

In [20]:
from pyspark.ml.classification import DecisionTreeClassifier
dt = DecisionTreeClassifier(labelCol="label", featuresCol="features", maxDepth=5)
dtModel = dt.fit(trainingData)
print("numNodes = ", dtModel.numNodes)
print("depth = ", dtModel.depth)
predictions = dtModel.transform(testData)
display(predictions)

label Estimated_CareMoments_Weekly Estimated_Minutes_Weekly Advice_Instructions_Travel Treatments Case_management Monitoring_Bevaking psychosocial_num physiological_num healthRelated_num ass_week_num ass_year_day register_NextWeekNR duration_mean_each_time duration_median_each_time care_times_weekly duration_week_minus duration_each_time Age ass_date ass_weekday ass_month ass_month_day ass_quater_day reg_date reg_weekDay reg_month reg_month_day reg_quater_day estimated_care_duration_Less_than_3_months estimated_care_duration_Longer_than_6_months estimated_care_request_Decreasing_Care estimated_care_request_Increasing_Care estimated_care_request_Stable_care_demand TeamID_0 ProblemName_Personal_care ProblemName_Skin combindSymptonProblemomittedSymptons rawFeatures features rawPrediction probability prediction 1.0 -2.42835361278535 -4.41505692051643 0.0 0.0 0.0 1.0 -1.07489125583662 -0.422573857940944 -1.28887010925821 30.0 209.0 31.0 -0.333472735371121 -0.596537638605271 -1.64879034295031 -1.71727082156315 1.16676467167333 0.900367377727457 28.0 6.0 7.0 28.0 28.0 26.0 4.0 7.0 26.0 26.0 1.88794608126386 -0.617985482268058 -0.661820249334744 -0.776632715218068 -0.406120359112696 0.54016919192849 -0.330597037409831 2.90520742954084 -1.14195356170005 List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, -0.422573857940944, -1.28887010925821, 30.0, 209.0, 31.0, -0.333472735371121, -0.596537638605271, -1.64879034295031, -1.71727082156315, 1.16676467167333, 0.900367377727457, 28.0, 6.0, 7.0, 28.0, 28.0, 26.0, 4.0, 7.0, 26.0, 26.0, 1.88794608126386, -0.617985482268058, -0.661820249334744, -0.776632715218068, -0.406120359112696, 0.54016919192849, -0.330597037409831, 2.90520742954084, -1.14195356170005)) List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, -0.422573857940944, -1.28887010925821, 30.0, 209.0, 31.0, -0.333472735371121, -0.596537638605271, -1.64879034295031, -1.71727082156315, 1.16676467167333, 0.900367377727457, 28.0, 6.0, 7.0, 28.0, 28.0, 26.0, 4.0, 7.0, 26.0, 26.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0)) List(1, 32, List(), List(0.0, 1155.0, 1368.0, 440.0, 330.0, 22.0, 4.0, 42.0, 0.0, 0.0, 0.0, 7.0, 7.0, 0.0, 0.0, 0.0, 2.0, 0.0, 0.0, 6.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 2.0, 0.0, 0.0)) List(1, 32, List(), List(0.0, 0.3412112259970458, 0.40413589364844904, 0.12998522895125553, 0.09748892171344166, 0.006499261447562777, 0.0011816838995568684, 0.012407680945347119, 0.0, 0.0, 0.0, 0.00206794682422452, 0.00206794682422452, 0.0, 0.0, 0.0, 5.908419497784342E-4, 0.0, 0.0, 0.0017725258493353029, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 0.0, 5.908419497784342E-4, 0.0, 0.0)) 2.0 1.0 -2.42835361278535 -4.41505692051643 0.0 0.0 0.0 1.0 -1.07489125583662 0.265702788042987 1.2690691336789 10.0 68.0 11.0 -0.686051986749209 -0.333889608030033 -2.43849521366943 -3.18127997658884 -0.857620455848467 1.0802194040719 9.0 5.0 3.0 9.0 68.0 9.0 5.0 3.0 9.0 68.0 -0.529675319282247 -0.617985482268058 -0.661820249334744 -0.776632715218068 -0.406120359112696 0.54016919192849 -0.330597037409831 -0.344208965326497 -1.14195356170005 List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, 0.265702788042987, 1.2690691336789, 10.0, 68.0, 11.0, -0.686051986749209, -0.333889608030033, -2.43849521366943, -3.18127997658884, -0.857620455848467, 1.0802194040719, 9.0, 5.0, 3.0, 9.0, 68.0, 9.0, 5.0, 3.0, 9.0, 68.0, -0.529675319282247, -0.617985482268058, -0.661820249334744, -0.776632715218068, -0.406120359112696, 0.54016919192849, -0.330597037409831, -0.344208965326497, -1.14195356170005)) List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, 0.265702788042987, 1.2690691336789, 10.0, 68.0, 11.0, -0.686051986749209, -0.333889608030033, -2.43849521366943, -3.18127997658884, -0.857620455848467, 1.0802194040719, 9.0, 5.0, 3.0, 9.0, 68.0, 9.0, 5.0, 3.0, 9.0, 68.0, 

In [21]:
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction", labelCol="label",metricName="f1")
print ("f1= ", evaluator.evaluate(predictions))
print("accuracy = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
print("weightedPrecision = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
print("weightedRecall = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

('f1= ', 0.2600503426961552)
('accuracy = ', 0.284964026908392)
('weightedPrecision = ', 0.26204414299638323)
('weightedRecall = ', 0.28496402690839195)

In [22]:
# Entropy and the Gini coefficient are the supported measures of impurity for Decision Trees. This is Gini by default. Changing this value is simple, model.setImpurity("Entropy").
dt.getImpurity()

Out[ 56 ]: 'gini'

grid search: decision tree

In [24]:
# from pyspark.ml.tuning import ParamGridBuilder, CrossValidator
# paramGrid = (ParamGridBuilder()
#              .addGrid(dt.maxDepth, [1, 2, 6, 10])
#              .addGrid(dt.maxBins, [20, 40, 80])
#              .build())

# cv = CrossValidator(estimator=dt, estimatorParamMaps=paramGrid, evaluator=evaluator, numFolds=5)
# cvModel = cv.fit(trainingData)
# print("numNodes = ", cvModel.bestModel.numNodes)
# print("depth = ", cvModel.bestModel.depth)
# predictions = cvModel.transform(testData)
# display(predictions)

In [25]:
# print ("f1= ", evaluator.evaluate(predictions))
# print("accuracy = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
# print("weightedPrecision = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
# print("weightedRecall = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

#random forest

In [27]:
# a simple random foreset 
from pyspark.ml.classification import RandomForestClassifier
rf = RandomForestClassifier(labelCol="label", featuresCol="features")
rfModel = rf.fit(trainingData)
predictions = rfModel.transform(testData)
display(predictions)

label Estimated_CareMoments_Weekly Estimated_Minutes_Weekly Advice_Instructions_Travel Treatments Case_management Monitoring_Bevaking psychosocial_num physiological_num healthRelated_num ass_week_num ass_year_day register_NextWeekNR duration_mean_each_time duration_median_each_time care_times_weekly duration_week_minus duration_each_time Age ass_date ass_weekday ass_month ass_month_day ass_quater_day reg_date reg_weekDay reg_month reg_month_day reg_quater_day estimated_care_duration_Less_than_3_months estimated_care_duration_Longer_than_6_months estimated_care_request_Decreasing_Care estimated_care_request_Increasing_Care estimated_care_request_Stable_care_demand TeamID_0 ProblemName_Personal_care ProblemName_Skin combindSymptonProblemomittedSymptons rawFeatures features rawPrediction probability prediction 1.0 -2.42835361278535 -4.41505692051643 0.0 0.0 0.0 1.0 -1.07489125583662 -0.422573857940944 -1.28887010925821 30.0 209.0 31.0 -0.333472735371121 -0.596537638605271 -1.64879034295031 -1.71727082156315 1.16676467167333 0.900367377727457 28.0 6.0 7.0 28.0 28.0 26.0 4.0 7.0 26.0 26.0 1.88794608126386 -0.617985482268058 -0.661820249334744 -0.776632715218068 -0.406120359112696 0.54016919192849 -0.330597037409831 2.90520742954084 -1.14195356170005 List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, -0.422573857940944, -1.28887010925821, 30.0, 209.0, 31.0, -0.333472735371121, -0.596537638605271, -1.64879034295031, -1.71727082156315, 1.16676467167333, 0.900367377727457, 28.0, 6.0, 7.0, 28.0, 28.0, 26.0, 4.0, 7.0, 26.0, 26.0, 1.88794608126386, -0.617985482268058, -0.661820249334744, -0.776632715218068, -0.406120359112696, 0.54016919192849, -0.330597037409831, 2.90520742954084, -1.14195356170005)) List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, -0.422573857940944, -1.28887010925821, 30.0, 209.0, 31.0, -0.333472735371121, -0.596537638605271, -1.64879034295031, -1.71727082156315, 1.16676467167333, 0.900367377727457, 28.0, 6.0, 7.0, 28.0, 28.0, 26.0, 4.0, 7.0, 26.0, 26.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0)) List(1, 32, List(), List(0.0, 5.571022782523816, 7.143995359556711, 3.5428928777999737, 1.4687139899038633, 0.7488362771663981, 0.5339489352449018, 0.297048214167245, 0.2210224892798, 0.08341961163248096, 0.057637181874508704, 0.07547755215414897, 0.03735600995452027, 0.034513814471440335, 0.021782352923483905, 0.011176294912647133, 0.007797356135566474, 0.01821771012127917, 0.03817068819694163, 0.005280877760185352, 0.0025968579631601017, 0.004665517995461661, 0.002636499324592668, 0.0, 0.012091711150617569, 0.007358225940086048, 0.02014127178296659, 0.007936507936507936, 7.215007215007215E-4, 0.01024805691942466, 3.0646149875802447E-4, 0.012987012987012988)) List(1, 32, List(), List(0.0, 0.27855113912619067, 0.3571997679778354, 0.17714464388999862, 0.07343569949519314, 0.03744181385831989, 0.026697446762245083, 0.014852410708362244, 0.011051124463989996, 0.004170980581624046, 0.002881859093725434, 0.0037738776077074474, 0.001867800497726013, 0.001725690723572016, 0.0010891176461741948, 5.588147456323565E-4, 3.898678067783236E-4, 9.108855060639582E-4, 0.001908534409847081, 2.640438880092675E-4, 1.2984289815800505E-4, 2.3327589977308296E-4, 1.3182496622963334E-4, 0.0, 6.045855575308782E-4, 3.679112970043023E-4, 0.0010070635891483292, 3.9682539682539666E-4, 3.607503607503606E-5, 5.124028459712329E-4, 1.5323074937901217E-5, 6.493506493506491E-4)) 2.0 1.0 -2.42835361278535 -4.41505692051643 0.0 0.0 0.0 1.0 -1.07489125583662 0.265702788042987 1.2690691336789 10.0 68.0 11.0 -0.686051986749209 -0.333889608030033 -2.43849521366943 -3.18127997658884 -0.857620455848467 1.0802194040719 9.0 5.0 3.0 9.0 68.0 9.0 5.0 3.0 9.0 68.0 -0.529675319282247 -0.617985482268058 -0.661820249334744 -0.776632715218068 -0.406120359112696 0.54016919192849 -0.330597037409831 -0.344208965326497 -1.14195356170005 List(1, 37, List(), List(-2.428353612785

In [28]:
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction", labelCol="label",metricName="f1")
print ("f1= ", evaluator.evaluate(predictions))
print("accuracy = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
print("weightedPrecision = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
print("weightedRecall = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

('f1= ', 0.29644856043937845)
('accuracy = ', 0.32663567180073244)
('weightedPrecision = ', 0.3575344145424953)
('weightedRecall = ', 0.32663567180073255)

grid search on random forest

In [30]:
# from pyspark.ml.tuning import ParamGridBuilder, CrossValidator

# paramGrid = (ParamGridBuilder()
#              .addGrid(rf.maxDepth, [10,20])
# #              .addGrid(rf.maxBins, [20, 60])
#              .addGrid(rf.numTrees, [1])
#              .build())
# cv = CrossValidator(estimator=rf, estimatorParamMaps=paramGrid, evaluator=evaluator, numFolds=5)

# cvModel = cv.fit(trainingData)
# predictions = cvModel.transform(testData)

# print ("f1= ", evaluator.evaluate(predictions))
# print("accuracy = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
# print("weightedPrecision = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
# print("weightedRecall = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

# bestModel = cvModel.bestModel
# # Generate predictions for entire dataset
# finalPredictions = bestModel.transform(df)
# # Evaluate best model
# print ("f1(entire dataset)= ", evaluator.evaluate(predictions))
# print("accuracy(entire dataset) = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
# print("precision(entire dataset) = ",evaluator.evaluate(predictions, {evaluator.metricName: "precision"}))
# print("recall(entire dataset) = ",evaluator.evaluate(predictions, {evaluator.metricName: "recall"}))
# print("weightedPrecision(entire dataset) = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
# print("weightedRecall(entire dataset) = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

# finalPredictions.createOrReplaceTempView("finalPredictions")

#Multilayer perceptron classifier
neural network structure 65inputs, 35 middle neuros, 20output

time-consuming

In [32]:
trainingData_temp = trainingData.select("features","label")
testData_temp = trainingData.select("features","label")

In [33]:
trainingData_temp.select("label").distinct().count()

Out[ 63 ]: 31

In [34]:
from pyspark.ml.classification import MultilayerPerceptronClassifier
from pyspark.ml.evaluation import MulticlassClassificationEvaluator

## use one hot encoding to encode output, so 22 classes will get the 23 numbers 000000000....001(the 22nd is 1,start from position 0)
layers = [35,2000,1000,500,100,32]
# create the trainer and set its parameters
trainer = MultilayerPerceptronClassifier(maxIter=100, layers=layers, blockSize=128, seed=1234)
model = trainer.fit(trainingData_temp)

# compute accuracy on the test set
result = model.transform(testData_temp)
predictionAndLabels = result.select("prediction", "label")
evaluator = MulticlassClassificationEvaluator(metricName="accuracy")
print("Test set accuracy = " + str(evaluator.evaluate(predictionAndLabels)))


java.net.ConnectException: Connection refused
	at sun.nio.ch.SocketChannelImpl.checkConnect(Native Method)
	at sun.nio.ch.SocketChannelImpl.finishConnect(SocketChannelImpl.java:717)
	at sun.nio.ch.SocketAdaptor.connect(SocketAdaptor.java:111)
	at org.eclipse.jetty8.client.SelectConnector.startConnection(SelectConnector.java:82)
	at org.eclipse.jetty8.client.HttpDestination.startNewConnection(HttpDestination.java:292)
	at org.eclipse.jetty8.client.HttpDestination.doSend(HttpDestination.java:597)
	at org.eclipse.jetty8.client.HttpDestination.send(HttpDestination.java:532)
	at org.eclipse.jetty8.client.HttpClient.send(HttpClient.java:180)
	at com.databricks.rpc.JettyClient.$anonfun$sendRawExchange$2(JettyClient.scala:244)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:12)
	at com.databricks.logging.UsageLogging.$anonfun$withAttributionContext$1(UsageLogging.scala:188)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:58)
	at com.databricks.logging.UsageLogging.withAttributionContext(UsageLogging.scala:183)
	at com.databricks.logging.UsageLogging.withAttributionContext$(UsageLogging.scala:180)
	at com.databricks.rpc.JettyClient.withAttributionContext(JettyClient.scala:32)
	at com.databricks.rpc.JettyClient.sendRawExchange(JettyClient.scala:234)
	at com.databricks.rpc.JettyClient.sendExchange(JettyClient.scala:164)
	at com.databricks.rpc.JettyClient.sendAsync(JettyClient.scala:101)
	at com.databricks.rpc.BoundRPCClient.sendAsync(BoundRPCClient.scala:47)
	at com.databricks.backend.daemon.driver.DriverClient.com$databricks$backend$daemon$driver$DriverClient$$send(DriverClient.scala:95)
	at com.databricks.backend.daemon.driver.DriverClient.$anonfun$poll$1(DriverClient.scala:283)
	at com.databricks.util.FutureUtils$.retry(FutureUtils.scala:89)
	at com.databricks.util.FutureUtils$$anonfun$retry$2.applyOrElse(FutureUtils.scala:93)
	at com.databricks.util.FutureUtils$$anonfun$retry$2.applyOrElse(FutureUtils.scala:91)
	at scala.concurrent.Future.$anonfun$recoverWith$1(Future.scala:413)
	at scala.concurrent.impl.Promise.$anonfun$transformWith$1(Promise.scala:37)
	at scala.concurrent.impl.CallbackRunnable.run(Promise.scala:60)
	at com.databricks.threading.NamedExecutor$$anon$2.$anonfun$run$1(NamedExecutor.scala:292)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:12)
	at com.databricks.logging.UsageLogging.$anonfun$withAttributionContext$1(UsageLogging.scala:188)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:58)
	at com.databricks.logging.UsageLogging.withAttributionContext(UsageLogging.scala:183)
	at com.databricks.logging.UsageLogging.withAttributionContext$(UsageLogging.scala:180)
	at com.databricks.threading.NamedExecutor.withAttributionContext(NamedExecutor.scala:241)
	at com.databricks.threading.NamedExecutor$$anon$2.run(NamedExecutor.scala:292)
	at java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1149)
	at java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:624)
	at java.lang.Thread.run(Thread.java:748)

In [35]:
print ("f1= ", evaluator.evaluate(predictionAndLabels,{evaluator.metricName: "f1"}))
print("accuracy = ",evaluator.evaluate(predictionAndLabels, {evaluator.metricName: "accuracy"}))
print("weightedPrecision = ",evaluator.evaluate(predictionAndLabels, {evaluator.metricName: "weightedPrecision"}))
print("weightedRecall = ",evaluator.evaluate(predictionAndLabels, {evaluator.metricName: "weightedRecall"}))

java.net.ConnectException: Connection refused
	at sun.nio.ch.SocketChannelImpl.checkConnect(Native Method)
	at sun.nio.ch.SocketChannelImpl.finishConnect(SocketChannelImpl.java:717)
	at sun.nio.ch.SocketAdaptor.connect(SocketAdaptor.java:111)
	at org.eclipse.jetty8.client.SelectConnector.startConnection(SelectConnector.java:82)
	at org.eclipse.jetty8.client.HttpDestination.startNewConnection(HttpDestination.java:292)
	at org.eclipse.jetty8.client.HttpDestination.doSend(HttpDestination.java:597)
	at org.eclipse.jetty8.client.HttpDestination.send(HttpDestination.java:532)
	at org.eclipse.jetty8.client.HttpClient.send(HttpClient.java:180)
	at com.databricks.rpc.JettyClient.$anonfun$sendRawExchange$2(JettyClient.scala:244)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:12)
	at com.databricks.logging.UsageLogging.$anonfun$withAttributionContext$1(UsageLogging.scala:188)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:58)
	at com.databricks.logging.UsageLogging.withAttributionContext(UsageLogging.scala:183)
	at com.databricks.logging.UsageLogging.withAttributionContext$(UsageLogging.scala:180)
	at com.databricks.rpc.JettyClient.withAttributionContext(JettyClient.scala:32)
	at com.databricks.rpc.JettyClient.sendRawExchange(JettyClient.scala:234)
	at com.databricks.rpc.JettyClient.sendExchange(JettyClient.scala:164)
	at com.databricks.rpc.JettyClient.sendAsync(JettyClient.scala:101)
	at com.databricks.rpc.BoundRPCClient.sendAsync(BoundRPCClient.scala:47)
	at com.databricks.backend.daemon.driver.DriverClient.com$databricks$backend$daemon$driver$DriverClient$$send(DriverClient.scala:95)
	at com.databricks.backend.daemon.driver.DriverClient.$anonfun$poll$1(DriverClient.scala:283)
	at com.databricks.util.FutureUtils$.retry(FutureUtils.scala:89)
	at com.databricks.util.FutureUtils$$anonfun$retry$2.applyOrElse(FutureUtils.scala:93)
	at com.databricks.util.FutureUtils$$anonfun$retry$2.applyOrElse(FutureUtils.scala:91)
	at scala.concurrent.Future.$anonfun$recoverWith$1(Future.scala:413)
	at scala.concurrent.impl.Promise.$anonfun$transformWith$1(Promise.scala:37)
	at scala.concurrent.impl.CallbackRunnable.run(Promise.scala:60)
	at com.databricks.threading.NamedExecutor$$anon$2.$anonfun$run$1(NamedExecutor.scala:292)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:12)
	at com.databricks.logging.UsageLogging.$anonfun$withAttributionContext$1(UsageLogging.scala:188)
	at scala.util.DynamicVariable.withValue(DynamicVariable.scala:58)
	at com.databricks.logging.UsageLogging.withAttributionContext(UsageLogging.scala:183)
	at com.databricks.logging.UsageLogging.withAttributionContext$(UsageLogging.scala:180)
	at com.databricks.threading.NamedExecutor.withAttributionContext(NamedExecutor.scala:241)
	at com.databricks.threading.NamedExecutor$$anon$2.run(NamedExecutor.scala:292)
	at java.util.concurrent.ThreadPoolExecutor.runWorker(ThreadPoolExecutor.java:1149)
	at java.util.concurrent.ThreadPoolExecutor$Worker.run(ThreadPoolExecutor.java:624)
	at java.lang.Thread.run(Thread.java:748)

#One-vs-Rest classifier (a.k.a. One-vs-All)

In [37]:
from pyspark.ml.classification import LogisticRegression, OneVsRest

lr = LogisticRegression(maxIter=10, tol=1E-6, fitIntercept=True,labelCol="label", featuresCol="features")
ovr = OneVsRest(classifier=lr)
ovrModel = ovr.fit(trainingData)
predictions = ovrModel.transform(testData)
display(predictions)

label Estimated_CareMoments_Weekly Estimated_Minutes_Weekly Advice_Instructions_Travel Treatments Case_management Monitoring_Bevaking psychosocial_num physiological_num healthRelated_num ass_week_num ass_year_day register_NextWeekNR duration_mean_each_time duration_median_each_time care_times_weekly duration_week_minus duration_each_time Age ass_date ass_weekday ass_month ass_month_day ass_quater_day reg_date reg_weekDay reg_month reg_month_day reg_quater_day estimated_care_duration_Less_than_3_months estimated_care_duration_Longer_than_6_months estimated_care_request_Decreasing_Care estimated_care_request_Increasing_Care estimated_care_request_Stable_care_demand TeamID_0 ProblemName_Personal_care ProblemName_Skin combindSymptonProblemomittedSymptons rawFeatures features prediction 1.0 -2.42835361278535 -4.41505692051643 0.0 0.0 0.0 1.0 -1.07489125583662 -0.422573857940944 -1.28887010925821 30.0 209.0 31.0 -0.333472735371121 -0.596537638605271 -1.64879034295031 -1.71727082156315 1.16676467167333 0.900367377727457 28.0 6.0 7.0 28.0 28.0 26.0 4.0 7.0 26.0 26.0 1.88794608126386 -0.617985482268058 -0.661820249334744 -0.776632715218068 -0.406120359112696 0.54016919192849 -0.330597037409831 2.90520742954084 -1.14195356170005 List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, -0.422573857940944, -1.28887010925821, 30.0, 209.0, 31.0, -0.333472735371121, -0.596537638605271, -1.64879034295031, -1.71727082156315, 1.16676467167333, 0.900367377727457, 28.0, 6.0, 7.0, 28.0, 28.0, 26.0, 4.0, 7.0, 26.0, 26.0, 1.88794608126386, -0.617985482268058, -0.661820249334744, -0.776632715218068, -0.406120359112696, 0.54016919192849, -0.330597037409831, 2.90520742954084, -1.14195356170005)) List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, -0.422573857940944, -1.28887010925821, 30.0, 209.0, 31.0, -0.333472735371121, -0.596537638605271, -1.64879034295031, -1.71727082156315, 1.16676467167333, 0.900367377727457, 28.0, 6.0, 7.0, 28.0, 28.0, 26.0, 4.0, 7.0, 26.0, 26.0, 1.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 1.0, 0.0)) 1.0 1.0 -2.42835361278535 -4.41505692051643 0.0 0.0 0.0 1.0 -1.07489125583662 0.265702788042987 1.2690691336789 10.0 68.0 11.0 -0.686051986749209 -0.333889608030033 -2.43849521366943 -3.18127997658884 -0.857620455848467 1.0802194040719 9.0 5.0 3.0 9.0 68.0 9.0 5.0 3.0 9.0 68.0 -0.529675319282247 -0.617985482268058 -0.661820249334744 -0.776632715218068 -0.406120359112696 0.54016919192849 -0.330597037409831 -0.344208965326497 -1.14195356170005 List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, 0.265702788042987, 1.2690691336789, 10.0, 68.0, 11.0, -0.686051986749209, -0.333889608030033, -2.43849521366943, -3.18127997658884, -0.857620455848467, 1.0802194040719, 9.0, 5.0, 3.0, 9.0, 68.0, 9.0, 5.0, 3.0, 9.0, 68.0, -0.529675319282247, -0.617985482268058, -0.661820249334744, -0.776632715218068, -0.406120359112696, 0.54016919192849, -0.330597037409831, -0.344208965326497, -1.14195356170005)) List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, 0.265702788042987, 1.2690691336789, 10.0, 68.0, 11.0, -0.686051986749209, -0.333889608030033, -2.43849521366943, -3.18127997658884, -0.857620455848467, 1.0802194040719, 9.0, 5.0, 3.0, 9.0, 68.0, 9.0, 5.0, 3.0, 9.0, 68.0, 0.0, 0.0, 0.0, 0.0, 0.0, 1.0, 0.0, 0.0, 0.0)) 1.0 1.0 -2.42835361278535 -4.41505692051643 0.0 0.0 0.0 1.0 -1.07489125583662 0.265702788042987 1.2690691336789 10.0 68.0 11.0 -0.686051986749209 -0.333889608030033 -2.43849521366943 -3.18127997658884 -0.857620455848467 1.0802194040719 9.0 5.0 3.0 9.0 68.0 9.0 5.0 3.0 9.0 68.0 -0.529675319282247 -0.617985482268058 -0.661820249334744 -0.776632715218068 -0.406120359112696 0.54016919192849 -0.330597037409831 -0.344208965326497 -1.14195356170005 List(1, 37, List(), List(-2.42835361278535, -4.41505692051643, 0.0, 0.0, 0.0, 1.0, -1.07489125583662, 0.2657027880429

In [38]:
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction", labelCol="label",metricName="f1")
print ("f1= ", evaluator.evaluate(predictions))
print("accuracy = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
print("weightedPrecision = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
print("weightedRecall = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

('f1= ', 0.2286419066945916)
('accuracy = ', 0.23880938157450457)
('weightedPrecision = ', 0.24923232453034272)
('weightedRecall = ', 0.23880938157450451)

#one-hot encoding here not in R, then use randomForest

In [40]:
sqlContext.clearCache()
from pyspark.sql.types import StructType, StructField, IntegerType, StringType
# df = sqlContext.read.format('csv').options(header='true').load("/FileStore/tables/allCom_60_v2.csv").drop("PatientID").withColumnRenamed('duration_next_week_category','label')
###
df = (sqlContext.read.format('csv').options(header='true')
      .load("/FileStore/tables/allCom_60_raw_18.csv")
      .withColumnRenamed('duration_next_week_category','label')).drop("TeamID").drop("SignAndSymptomName").drop("ProblemName")
df.cache()

df.printSchema()

root
-- register_WeekNR: string (nullable = true)
-- estimated_care_duration: string (nullable = true)
-- estimated_care_request: string (nullable = true)
-- Estimated_CareMoments_Weekly: string (nullable = true)
-- Estimated_Minutes_Weekly: string (nullable = true)
-- Case_management: string (nullable = true)
-- psychosocial_num: string (nullable = true)
-- physiological_num: string (nullable = true)
-- healthRelated_num: string (nullable = true)
-- ass_year_day: string (nullable = true)
-- duration_mean_each_time: string (nullable = true)
-- duration_median_each_time: string (nullable = true)
-- care_times_weekly: string (nullable = true)
-- duration_week_minus: string (nullable = true)
-- Financer: string (nullable = true)
-- duration_each_time: string (nullable = true)
-- Problem_EndTime: string (nullable = true)
-- Age: string (nullable = true)
-- Gender: string (nullable = true)
-- Marital_status: string (nullable = true)
-- Living_unit: string (nullable = true)
-- label: string (nullable = true)

In [41]:
#estimated_care_request,Financer,TeamID,SignAndSymptomName,ProblemName,Gender,Marital_status,Living_unit
df =df.drop("Problem_EndTime")

from pyspark.ml import Pipeline
from pyspark.ml.feature import StringIndexer

indexers = [StringIndexer(inputCol=column, outputCol=column+"_index")
            .fit(df) for column in list(
                set(df.columns)-
                set(['register_WeekNR','Estimated_CareMoments_Weekly','Estimated_Minutes_Weekly',
                     'healthRelated_num','psychosocial_num','physiological_num','ass_year_day',
                     'duration_mean_each_time','duration_median_each_time','care_times_weekly',
                     'duration_week_minus','duration_each_time','Age','label'])) ]
pipeline = Pipeline(stages=indexers)
train_catind = pipeline.fit(df).transform(df)
# train_catind.show()
from pyspark.ml.feature import OneHotEncoder, StringIndexer
indexers_ON = [OneHotEncoder(inputCol=column, outputCol=column+"_Vec") for column in filter(lambda x: x.endswith('_index'), 
                                                                                            train_catind.columns) ]
pipeline = Pipeline(stages=indexers_ON)
train_OHE = pipeline.fit(train_catind).transform(train_catind)
train_OHE.show()

train_OHE = train_OHE.withColumn("register_WeekNR", train_OHE["register_WeekNR"].cast("double"))
train_OHE = train_OHE.withColumn("Estimated_CareMoments_Weekly", train_OHE["Estimated_CareMoments_Weekly"].cast("double"))
train_OHE = train_OHE.withColumn("Estimated_Minutes_Weekly", train_OHE["Estimated_Minutes_Weekly"].cast("double"))
train_OHE = train_OHE.withColumn("healthRelated_num", train_OHE["healthRelated_num"].cast("double"))
train_OHE = train_OHE.withColumn("psychosocial_num", train_OHE["psychosocial_num"].cast("double"))
train_OHE = train_OHE.withColumn("physiological_num", train_OHE["physiological_num"].cast("double"))
train_OHE = train_OHE.withColumn("ass_year_day", train_OHE["ass_year_day"].cast("double"))
train_OHE = train_OHE.withColumn("duration_mean_each_time", train_OHE["duration_mean_each_time"].cast("double"))
train_OHE = train_OHE.withColumn("duration_median_each_time", train_OHE["duration_median_each_time"].cast("double"))
train_OHE = train_OHE.withColumn("care_times_weekly", train_OHE["care_times_weekly"].cast("double"))
train_OHE = train_OHE.withColumn("duration_week_minus", train_OHE["duration_week_minus"].cast("double"))
train_OHE = train_OHE.withColumn("duration_each_time", train_OHE["duration_each_time"].cast("double"))
train_OHE = train_OHE.withColumn("Age", train_OHE["Age"].cast("double"))
train_OHE = train_OHE.withColumn("label", train_OHE["label"].cast("double"))

from pyspark.ml.feature import VectorAssembler
from pyspark.ml.classification import RandomForestClassifier

#use VectorAssembler to combine all the feature columns into a single vector column
assemblerInputs = ['register_WeekNR','Estimated_CareMoments_Weekly',
                   'Estimated_Minutes_Weekly','healthRelated_num','psychosocial_num',
                   'physiological_num','ass_year_day','duration_mean_each_time',
                   'duration_median_each_time','care_times_weekly',
                   'duration_week_minus','duration_each_time','Age',
                   "Case_management_index_Vec","Gender_index_Vec",
                   "Marital_status_index_Vec","Living_unit_index_Vec",
                   "estimated_care_request_index_Vec",
                   "Financer_index_Vec","estimated_care_duration_index_Vec"]
vectorAssembler = VectorAssembler(inputCols=assemblerInputs, outputCol="features")
pipeline = Pipeline(stages=[vectorAssembler])
pipelineModel = pipeline.fit(train_OHE)
df = pipelineModel.transform(train_OHE)
(trainingData, testData) = df.randomSplit([0.7, 0.3], seed=100)

rf = RandomForestClassifier(labelCol="label", featuresCol="features")
rf_model = rf.fit(trainingData)
predictions = rf_model.transform(trainingData)
display(predictions)

register_WeekNR estimated_care_duration estimated_care_request Estimated_CareMoments_Weekly Estimated_Minutes_Weekly Case_management psychosocial_num physiological_num healthRelated_num ass_year_day duration_mean_each_time duration_median_each_time care_times_weekly duration_week_minus Financer duration_each_time Age Gender Marital_status Living_unit label Case_management_index Gender_index Marital_status_index Living_unit_index estimated_care_request_index Financer_index estimated_care_duration_index Case_management_index_Vec Gender_index_Vec Marital_status_index_Vec Living_unit_index_Vec estimated_care_request_index_Vec Financer_index_Vec estimated_care_duration_index_Vec features rawPrediction probability prediction 1.0 3 to 6 months Decreasing Care 7.0 255.0 0 0.0 0.0 0.0 5.0 27.5 22.5 4.0 110.0 ZVW 15.0 83.0 F Samenwonend Single person 1.0 1.0 0.0 1.0 0.0 1.0 0.0 3.0 List(0, 1, List(), List()) List(0, 1, List(0), List(1.0)) List(0, 4, List(1), List(1.0)) List(0, 7, List(0), List(1.0)) List(0, 3, List(1), List(1.0)) List(0, 6, List(0), List(1.0)) List(0, 3, List(), List()) List(0, 38, List(0, 1, 2, 6, 7, 8, 9, 10, 11, 12, 14, 16, 19, 27, 29), List(1.0, 7.0, 255.0, 5.0, 27.5, 22.5, 4.0, 110.0, 15.0, 83.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 18, List(), List(0.0, 2.87660854252343, 5.495437814471064, 4.818734256982478, 3.4717609977618498, 1.4696027986296023, 0.7124033844467412, 0.41914713513798857, 0.23414476322451996, 0.19350381479344486, 0.08331750768052124, 0.06309665025580992, 0.024706255206822677, 0.08925999822108889, 0.020589240240688214, 0.01566595136491864, 0.009652718050515353, 0.002368171008516604)) List(1, 18, List(), List(0.0, 0.14383042712617145, 0.27477189072355307, 0.24093671284912382, 0.17358804988809243, 0.07348013993148009, 0.03562016922233705, 0.02095735675689942, 0.011707238161225994, 0.00967519073967224, 0.00416587538402606, 0.0031548325127904947, 0.0012353127603411335, 0.004462999911054443, 0.0010294620120344104, 7.832975682459318E-4, 4.826359025257675E-4, 1.1840855042583017E-4)) 2.0 1.0 3 to 6 months Decreasing Care 7.0 255.0 0 0.0 0.0 0.0 5.0 27.5 22.5 4.0 110.0 ZVW 15.0 83.0 F Samenwonend Single person 1.0 1.0 0.0 1.0 0.0 1.0 0.0 3.0 List(0, 1, List(), List()) List(0, 1, List(0), List(1.0)) List(0, 4, List(1), List(1.0)) List(0, 7, List(0), List(1.0)) List(0, 3, List(1), List(1.0)) List(0, 6, List(0), List(1.0)) List(0, 3, List(), List()) List(0, 38, List(0, 1, 2, 6, 7, 8, 9, 10, 11, 12, 14, 16, 19, 27, 29), List(1.0, 7.0, 255.0, 5.0, 27.5, 22.5, 4.0, 110.0, 15.0, 83.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 18, List(), List(0.0, 2.87660854252343, 5.495437814471064, 4.818734256982478, 3.4717609977618498, 1.4696027986296023, 0.7124033844467412, 0.41914713513798857, 0.23414476322451996, 0.19350381479344486, 0.08331750768052124, 0.06309665025580992, 0.024706255206822677, 0.08925999822108889, 0.020589240240688214, 0.01566595136491864, 0.009652718050515353, 0.002368171008516604)) List(1, 18, List(), List(0.0, 0.14383042712617145, 0.27477189072355307, 0.24093671284912382, 0.17358804988809243, 0.07348013993148009, 0.03562016922233705, 0.02095735675689942, 0.011707238161225994, 0.00967519073967224, 0.00416587538402606, 0.0031548325127904947, 0.0012353127603411335, 0.004462999911054443, 0.0010294620120344104, 7.832975682459318E-4, 4.826359025257675E-4, 1.1840855042583017E-4)) 2.0 1.0 3 to 6 months Decreasing Care 7.0 255.0 0 0.0 0.0 0.0 5.0 27.5 22.5 4.0 110.0 ZVW 15.0 83.0 F Samenwonend Single person 1.0 1.0 0.0 1.0 0.0 1.0 0.0 3.0 List(0, 1, List(), List()) List(0, 1, List(0), List(1.0)) List(0, 4, List(1), List(1.0)) List(0, 7, List(0), List(1.0)) List(0, 3, List(1), List(1.0)) List(0, 6, List(0), List(1.0)) List(0, 3, List(), List()) List(0, 38, List(0, 1, 2, 6, 7, 8, 9, 10, 11, 12, 14, 16, 19, 27, 29), List(1.0, 7.0, 255.0, 5.0, 27.5, 22.5, 4.0, 110.0, 15.0, 83.0, 1.0, 1.0, 1.0, 1.0, 1.0)) List(1, 18, List(), List(0.0, 2.87660854252343, 5.495437814471064, 4.818734256982478, 3.4717609977618498, 1.4696027986296023

In [42]:
from pyspark.ml.evaluation import MulticlassClassificationEvaluator
evaluator = MulticlassClassificationEvaluator(predictionCol="prediction", labelCol="label",metricName="f1")
print ("f1= ", evaluator.evaluate(predictions))
print("accuracy = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
print("weightedPrecision = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
print("weightedRecall = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

('f1= ', 0.3346944341651985)
('accuracy = ', 0.35125260829280175)
('weightedPrecision = ', 0.4493817795932005)
('weightedRecall = ', 0.35125260829280175)

In [43]:
predictions = rf_model.transform(df)
print ("f1= ", evaluator.evaluate(predictions))
print("accuracy = ",evaluator.evaluate(predictions, {evaluator.metricName: "accuracy"}))
print("weightedPrecision = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedPrecision"}))
print("weightedRecall = ",evaluator.evaluate(predictions, {evaluator.metricName: "weightedRecall"}))

('f1= ', 0.33413215957164555)
('accuracy = ', 0.3508353389790282)
('weightedPrecision = ', 0.4488083198525757)
('weightedRecall = ', 0.35083533897902824)